In [1]:
!pip install -q transformers[torch] datasets
!pip install fasttext-langdetect
!pip install datasets

DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\morfessor-2.0.6-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330
DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\polyglot-16.7.4-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330


  Using cached fasttext_langdetect-1.0.5-py3-none-any.whl
  Using cached fasttext-0.9.2.tar.gz (68 kB)
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Running setup.py clean for fasttext
Failed to build fasttext


DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\morfessor-2.0.6-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330
DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\polyglot-16.7.4-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330
  error: subprocess-exited-with-error
  
  × python setup.py bdist_wheel did not run successfully.
  │ exit code: 1
  ╰─> [75 lines of output]
      C:\Users\jorge\miniconda3\Lib\site-packages\setuptools\dist.py:498: SetuptoolsDeprecationWarning: Invalid dash-separated options
      !!
      
              ********************************************************************************
              Usage of dash-s

DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\morfessor-2.0.6-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330
DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\polyglot-16.7.4-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330


In [2]:
!pip install -U pip wheel
!pip install ensemble-transformers

  Using cached pip-24.0-py3-none-any.whl.metadata (3.6 kB)
  Using cached wheel-0.43.0-py3-none-any.whl.metadata (2.2 kB)
Using cached pip-24.0-py3-none-any.whl (2.1 MB)
Using cached wheel-0.43.0-py3-none-any.whl (65 kB)


DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\morfessor-2.0.6-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330
DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\polyglot-16.7.4-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330
ERROR: To modify pip, please run the following command:
C:\Users\jorge\miniconda3\python.exe -m pip install -U pip wheel


DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\morfessor-2.0.6-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330
DEPRECATION: Loading egg at c:\users\jorge\miniconda3\lib\site-packages\polyglot-16.7.4-py3.12.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330


# Imports

In [1]:
from sklearn.model_selection import train_test_split
import pandas as pd
from datasets import load_dataset
from datasets import Dataset

c:\Users\jorge\miniconda3\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Load Dataset

In [2]:
from google.colab import drive
drive.mount('/content/drive')

ModuleNotFoundError: No module named 'google.colab'

In [2]:
from datasets import Dataset

dataset_en = Dataset.from_json("/content/drive/MyDrive/2024/test/subtask_1/test.jsonl")

dataset_en

FileNotFoundError: Unable to find '/content/drive/MyDrive/2024/test/subtask_1/test.jsonl'

# Test 2024

## Transformers langs

In [ ]:
from ftlangdetect import detect
import re

# Initialize an empty dictionary to store the texts for each language
language_datasets = {}
languages = ["en", "es", "ca", "pt", "eu", "gl"]

# Assuming dataset_en is a list of texts
for id_t,text in zip(dataset_en['id'], dataset_en['text']):
    try:

        language = detect(text)
    except:
        language = "Error, could not detect"

    # If the language is not already a key in the dictionary, add it with an empty list as its value
    if language['lang'] not in languages:
        if language['lang'] == 'it':
            language['lang'] = 'pt'
        elif language['lang'] == 'fr':
            language['lang'] = 'ca'
        else:
            language['lang'] = 'es'

    if language['lang'] not in language_datasets:
        language_datasets[language['lang']] = []

    # Append the text to the list of texts for its detected language
    language_datasets[language['lang']].append((id_t,text))

In [ ]:
# Set your threshold
threshold = 1000

# Create a new dictionary with only the items where the length of the list is greater than or equal to the threshold
#language_datasets = {language: texts for language, texts in language_datasets.items() if len(texts) >= threshold}

# Assuming language_datasets is your dictionary of languages and texts
for language, texts in language_datasets.items():
    print(f"Language: {language}, Number of texts: {len(texts)}")

Language: en, Number of texts: 10324
Language: ca, Number of texts: 8013
Language: pt, Number of texts: 9003
Language: es, Number of texts: 9116
Language: eu, Number of texts: 5518
Language: gl, Number of texts: 1391


In [ ]:
import pandas as pd

# Dictionary to store DataFrames
dataframes = {}

label_mapping = {"human": 0, "generated": 1}

def map_labels(example):
        # Map the original label to the new label
        example["label"] = label_mapping[example["label"]]
        return example

# Convert each list of tuples to DataFrame
for lang, data in language_datasets.items():
    df = pd.DataFrame(data, columns=['id', 'text'])

    dataframes[lang] = Dataset.from_pandas(df)

dataframes

{'en': Dataset({
     features: ['id', 'text'],
     num_rows: 10324
 }),
 'ca': Dataset({
     features: ['id', 'text'],
     num_rows: 8013
 }),
 'pt': Dataset({
     features: ['id', 'text'],
     num_rows: 9003
 }),
 'es': Dataset({
     features: ['id', 'text'],
     num_rows: 9116
 }),
 'eu': Dataset({
     features: ['id', 'text'],
     num_rows: 5518
 }),
 'gl': Dataset({
     features: ['id', 'text'],
     num_rows: 1391
 })}

In [ ]:
model_langs_names = {}

model_langs_names['en'] = "jorgefg03/albert-base-v2-autext2024"
model_langs_names['pt'] = "jorgefg03/bert-base-portuguese-cased-autext2024"
model_langs_names['es'] = "jorgefg03/roberta-base-bne-autext2024"
model_langs_names['gl'] = "jorgefg03/bert-galician-autext2024"
model_langs_names['eu'] = "jorgefg03/RoBasquERTa-autext2024"
model_langs_names['ca'] = "jorgefg03/roberta-base-ca-autext2024"
model_langs

{'en': 'jorgefg03/albert-base-v2-autext2024',
 'pt': 'jorgefg03/bert-base-portuguese-cased-autext2024',
 'es': 'jorgefg03/roberta-base-bne-autext2024',
 'gl': 'jorgefg03/bert-galician-autext2024',
 'eu': 'jorgefg03/RoBasquERTa-autext2024',
 'ca': 'jorgefg03/roberta-base-ca-autext2024'}

In [ ]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification

languages = ["en", "es", "ca", "pt", "eu", "gl"]
tokenizer_langs = {}
models_langs = {}


for lang in languages:
  tokenizer_langs[lang] = AutoTokenizer.from_pretrained(model_langs[lang])
  models_langs[lang] = AutoModelForSequenceClassification.from_pretrained(model_langs[lang])
  models_langs[lang].to("cuda")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/1.22k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/760k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.27M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/286 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/242k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/730k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/755 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/439M [00:00<?, ?B/s]

In [ ]:
def get_prediction_from_model_probs(text, model, tokenizer, max_length = 256):
  inputs = tokenizer(text, padding="max_length", max_length=max_length, truncation= True, return_tensors="pt").to('cuda')
  pred = model(**inputs).logits
  probs = pred.softmax(1)

  return probs[0][1].item()

In [ ]:
import pickle

preds_langs = {}

prefix = 'tr'

for lang in languages:
  print('Predictions for lang '+ lang)
  preds_langs[lang] = [(id_t, get_prediction_from_model_probs(text, models_langs[lang], tokenizer_langs[lang])) for id_t, text in zip(dataframes[lang]['id'], dataframes[lang]['text'])]
  with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_test_{lang}.pkl", "wb") as f:
    pickle.dump(preds_langs[lang], f)

In [ ]:
# Set your custom threshold here
threshold = 0.5

# Get predictions based on the custom threshold

only_preds = [item[1] for item in preds_langs['es']]
#preds_bin = (only_preds[:,1] >= threshold).astype('int')
only_preds

## Transformers multilingual

In [8]:
from datasets import Dataset

dataset_test = Dataset.from_json("/content/drive/MyDrive/2024/test/subtask_1/test.jsonl")

dataset_test

Dataset({
    features: ['id', 'text'],
    num_rows: 43365
})

In [9]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification

model_name1 = "jorgefg03/xlm-roberta-base-autext2024"
model_name2 = "jorgefg03/mdeberta-v3-base-autext2024"
model_name3 = "jorgefg03/distilbert-base-multilingual-cased-autext2024"

tokenizer1 = AutoTokenizer.from_pretrained(model_name1)
model1 = AutoModelForSequenceClassification.from_pretrained(model_name1)
model1.to("cuda")

tokenizer2 = AutoTokenizer.from_pretrained(model_name2)
model2 = AutoModelForSequenceClassification.from_pretrained(model_name2)
model2.to("cuda")

tokenizer3 = AutoTokenizer.from_pretrained(model_name3)
model3 = AutoModelForSequenceClassification.from_pretrained(model_name3)
model3.to("cuda")



/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/1.15k [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/2.92M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/541M [00:00<?, ?B/s]

DistilBertForSequenceClassification(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(119547, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0-5): 6 x TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)


In [10]:
def get_prediction_from_model_probs(text, model, tokenizer, max_length = 256):
  inputs = tokenizer(text, padding="max_length", max_length=max_length, truncation= True, return_tensors="pt").to('cuda')
  pred = model(**inputs).logits
  probs = pred.softmax(1)

  return probs[0][1].item()

In [ ]:
import pickle

preds_langs = {}

prefix = 'multi'

print('Predictions 1')
preds1 = [(id_t, get_prediction_from_model_probs(text, model1, tokenizer1)) for id_t, text in zip(dataset_test['id'], dataset_test['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_test_roberta.pkl", "wb") as f:
  pickle.dump(preds1, f)

print('Predictions 2')
preds2 = [(id_t, get_prediction_from_model_probs(text, model2, tokenizer2)) for id_t, text in zip(dataset_test['id'], dataset_test['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_test_mdberta.pkl", "wb") as f:
  pickle.dump(preds2, f)

print('Predictions 3')
preds3 = [(id_t, get_prediction_from_model_probs(text, model3, tokenizer3)) for id_t, text in zip(dataset_test['id'], dataset_test['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_test_distilbert.pkl", "wb") as f:
  pickle.dump(preds3, f)

Predictions 1
Predictions 2
Predictions 3


### Probar ensembler

In [11]:
from datasets import Dataset
from datasets import DatasetDict, concatenate_datasets

dataset_train = Dataset.from_json("/content/drive/MyDrive/2024/train/subtask_1/train.jsonl")

dataset_train

Generating train split: 0 examples [00:00, ? examples/s]

Dataset({
    features: ['id', 'text', 'label'],
    num_rows: 109663
})

In [12]:
from datasets import Dataset

# Assuming you have dataset_en already loaded and containing the 'train' split

# Define a mapping from original labels to new labels
label_mapping = {"human": 0, "generated": 1}

# Function to replace labels
def map_labels(example):
    # Map the original label to the new label
    example["label"] = label_mapping[example["label"]]
    return example

# Map the labels in the 'train' split
dataset_train = dataset_train.map(map_labels)

custom_label_names = ["human", "generated"]

dataset_train

Map:   0%|          | 0/109663 [00:00<?, ? examples/s]

Dataset({
    features: ['id', 'text', 'label'],
    num_rows: 109663
})

In [13]:
split_size = 0.2

splits = dataset_train.train_test_split(test_size=split_size, seed=32)
splits2 = splits['train'].train_test_split(test_size=(split_size/(1-split_size)), seed=32)


In [14]:
dataset_train = DatasetDict({
    "train": splits2['train'],
    "validation": splits['test'],
    'test': splits2['test']
})

# Print the updated dataset
print(dataset_train)

DatasetDict({
    train: Dataset({
        features: ['id', 'text', 'label'],
        num_rows: 65797
    })
    validation: Dataset({
        features: ['id', 'text', 'label'],
        num_rows: 21933
    })
    test: Dataset({
        features: ['id', 'text', 'label'],
        num_rows: 21933
    })
})


In [15]:
LABELS = set(dataset_train['train']['label'])
NUM_LABELS = len(LABELS)
print('LABELS:', LABELS, 'num_labels:', NUM_LABELS )

LABELS: {0, 1} num_labels: 2


In [16]:
def get_prediction_from_model_probs(text, model, tokenizer, max_length = 256):
  inputs = tokenizer(text, padding="max_length", max_length=max_length, truncation= True, return_tensors="pt").to('cuda')
  pred = model(**inputs).logits
  probs = pred.softmax(1)

  return probs[0][1].item()

In [17]:
import pickle

preds_langs = {}

prefix = 'multi'

print('Predictions 1')
preds1 = [(id_t, get_prediction_from_model_probs(text, model1, tokenizer1)) for id_t, text in zip(dataset_train['validation']['id'], dataset_train['validation']['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_train_val_roberta.pkl", "wb") as f:
  pickle.dump(preds1, f)

print('Predictions 2')
preds2 = [(id_t, get_prediction_from_model_probs(text, model2, tokenizer2)) for id_t, text in zip(dataset_train['validation']['id'], dataset_train['validation']['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_train_val_mdberta.pkl", "wb") as f:
  pickle.dump(preds2, f)

print('Predictions 3')
preds3 = [(id_t, get_prediction_from_model_probs(text, model3, tokenizer3)) for id_t, text in zip(dataset_train['validation']['id'], dataset_train['validation']['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_train_val_distilbert.pkl", "wb") as f:
  pickle.dump(preds3, f)

Predictions 1
Predictions 2
Predictions 3


In [18]:
print('Predictions 1')
preds1 = [(id_t, get_prediction_from_model_probs(text, model1, tokenizer1)) for id_t, text in zip(dataset_train['test']['id'], dataset_train['test']['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_train_test_roberta.pkl", "wb") as f:
  pickle.dump(preds1, f)

print('Predictions 2')
preds2 = [(id_t, get_prediction_from_model_probs(text, model2, tokenizer2)) for id_t, text in zip(dataset_train['test']['id'], dataset_train['test']['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_train_test_mdberta.pkl", "wb") as f:
  pickle.dump(preds2, f)

print('Predictions 3')
preds3 = [(id_t, get_prediction_from_model_probs(text, model3, tokenizer3)) for id_t, text in zip(dataset_train['test']['id'], dataset_train['test']['text'])]
with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_train_test_distilbert.pkl", "wb") as f:
  pickle.dump(preds3, f)

Predictions 1
Predictions 2
Predictions 3


## SVM models

In [1]:
!pip install fasttext-langdetect
!pip install datasets
!pip install stopwordsiso
!pip install simplemma

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 68.8/68.8 kB 778.7 kB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Using cached pybind11-2.12.0-py3-none-any.whl (234 kB)
  Created wheel for fasttext-langdetect: filename=fasttext_langdetect-1.0.5-py3-none-any.whl size=7503 sha256=dc3dea0d6b70f2e41be67aa84082ee8af366b648ce8c2cb4b3596e1a209f6341
  Stored in directory: /root/.cache/pip/wheels/e6/5b/5d/47e2fd5c2ff1028722739ce35f365e8f6eeb89ec97aa63e621
  Created wheel for fasttext: filename=fasttext-0.9.2-cp310-cp310-linux_x86_64.whl size=4227139 sha256=369ab063b9835b9595008b03474269826262f2c5c1e94d7635944e599cc21edd
  Stored in directory: /root/.cache/pip/wheels/a5/13/75/f811c84a8ab36eedbaef977a6a58a98990e8e0f1967f98f394
Successfully built fasttext-langdetect fasttext
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.0/542.0 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 13.3 MB/s eta 0:00:00
     ━━━━

In [2]:
import nltk

nltk.download('stopwords')
nltk.download('punkt')

from nltk.corpus import stopwords
import stopwordsiso as stopwordsd
from nltk import word_tokenize
from nltk.stem.porter import PorterStemmer
from nltk.stem.snowball import EnglishStemmer, PortugueseStemmer, SpanishStemmer
import re
from simplemma import simple_tokenizer
from simplemma import text_lemmatizer

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [5]:
from datasets import Dataset

dataset_test = Dataset.from_json("/content/drive/MyDrive/2024/test/subtask_1/test.jsonl")

dataset_test

Generating train split: 0 examples [00:00, ? examples/s]

Dataset({
    features: ['id', 'text'],
    num_rows: 43365
})

In [6]:
from ftlangdetect import detect
import re

# Initialize an empty dictionary to store the texts for each language
language_datasets = {}
languages = ["en", "es", "ca", "pt", "eu", "gl"]

# Assuming dataset_en is a list of texts
for id_t,text in zip(dataset_test['id'], dataset_test['text']):
    try:

        language = detect(text)
    except:
        language = "Error, could not detect"

    # If the language is not already a key in the dictionary, add it with an empty list as its value
    if language['lang'] not in languages:
        if language['lang'] == 'it':
            language['lang'] = 'pt'
        elif language['lang'] == 'fr':
            language['lang'] = 'ca'
        else:
            language['lang'] = 'es'

    if language['lang'] not in language_datasets:
        language_datasets[language['lang']] = []

    # Append the text to the list of texts for its detected language
    language_datasets[language['lang']].append((id_t,text))

In [7]:
# Set your threshold
threshold = 1000

# Create a new dictionary with only the items where the length of the list is greater than or equal to the threshold
#language_datasets = {language: texts for language, texts in language_datasets.items() if len(texts) >= threshold}

# Assuming language_datasets is your dictionary of languages and texts
for language, texts in language_datasets.items():
    print(f"Language: {language}, Number of texts: {len(texts)}")

Language: en, Number of texts: 10324
Language: ca, Number of texts: 8013
Language: pt, Number of texts: 9003
Language: es, Number of texts: 9116
Language: eu, Number of texts: 5518
Language: gl, Number of texts: 1391


In [8]:
import pandas as pd

# Dictionary to store DataFrames
dataframes = {}

label_mapping = {"human": 0, "generated": 1}

def map_labels(example):
        # Map the original label to the new label
        example["label"] = label_mapping[example["label"]]
        return example

# Convert each list of tuples to DataFrame
for lang, data in language_datasets.items():
    df = pd.DataFrame(data, columns=['id', 'text'])

    dataframes[lang] = Dataset.from_pandas(df)

dataframes

{'en': Dataset({
     features: ['id', 'text'],
     num_rows: 10324
 }),
 'ca': Dataset({
     features: ['id', 'text'],
     num_rows: 8013
 }),
 'pt': Dataset({
     features: ['id', 'text'],
     num_rows: 9003
 }),
 'es': Dataset({
     features: ['id', 'text'],
     num_rows: 9116
 }),
 'eu': Dataset({
     features: ['id', 'text'],
     num_rows: 5518
 }),
 'gl': Dataset({
     features: ['id', 'text'],
     num_rows: 1391
 })}

In [9]:
import joblib

languages = ["en", "es", "ca", "pt", "eu", "gl"]

models_svm_lang = {}

for lang in languages:

  models_svm_lang[lang] = joblib.load(f"/content/drive/MyDrive/2024/models/full_model_{lang}.pkl")

models_svm_lang

{'en': Pipeline(steps=[('bow',
                  CountVectorizer(analyzer=<function clean_text_en at 0x79ce221d5f30>)),
                 ('tf', TfidfTransformer()), ('svm', SVC())]),
 'es': Pipeline(steps=[('bow',
                  CountVectorizer(analyzer=<function clean_text_es at 0x79ce221d6290>)),
                 ('tf', TfidfTransformer()), ('svm', SVC())]),
 'ca': Pipeline(steps=[('bow',
                  CountVectorizer(analyzer=<function clean_text_ca at 0x79ce221d4040>)),
                 ('tf', TfidfTransformer()), ('svm', SVC())]),
 'pt': Pipeline(steps=[('bow',
                  CountVectorizer(analyzer=<function clean_text_pt at 0x79ce2243bf40>)),
                 ('tf', TfidfTransformer()), ('svm', SVC())]),
 'eu': Pipeline(steps=[('bow',
                  CountVectorizer(analyzer=<function clean_text_eu at 0x79ce2243b880>)),
                 ('tf', TfidfTransformer()), ('svm', SVC())]),
 'gl': Pipeline(steps=[('bow',
                  CountVectorizer(analyzer=<function c

In [ ]:
import pickle

prefix = 'svm'

for lang in languages:

  X_test = dataframes[lang]['text']
  X_ids = dataframes[lang]['id']

  y_preds = models_svm_lang[lang].predict(X_test)

  svm_preds = [(id_t, pred) for id_t,pred in zip(X_ids, y_preds)]

  with open(f"/content/drive/MyDrive/2024/predictions/{prefix}_test_{lang}.pkl", "wb") as f:
    pickle.dump(svm_preds, f)



svm_preds[0:10]

# Ensemble

In [2]:
from datasets import Dataset
from datasets import DatasetDict, concatenate_datasets

dataset_train = Dataset.from_json("./train/subtask_1/train.jsonl")
dataset_test = Dataset.from_json("./test/subtask_1/test.jsonl")

# Assuming you have dataset_en already loaded and containing the 'train' split

# Define a mapping from original labels to new labels
label_mapping = {"human": 0, "generated": 1}

# Function to replace labels
def map_labels(example):
    # Map the original label to the new label
    example["label"] = label_mapping[example["label"]]
    return example

# Map the labels in the 'train' split
dataset_train = dataset_train.map(map_labels)

custom_label_names = ["human", "generated"]

split_size = 0.2

splits = dataset_train.train_test_split(test_size=split_size, seed=32)
splits2 = splits['train'].train_test_split(test_size=(split_size/(1-split_size)), seed=32)

dataset_train = DatasetDict({
    "train": splits2['train'],
    "validation": splits['test'],
    'test': splits2['test']
})

# Print the updated dataset
print(dataset_train)

print(dataset_test)

DatasetDict({
    train: Dataset({
        features: ['id', 'text', 'label'],
        num_rows: 65797
    })
    validation: Dataset({
        features: ['id', 'text', 'label'],
        num_rows: 21933
    })
    test: Dataset({
        features: ['id', 'text', 'label'],
        num_rows: 21933
    })
})
Dataset({
    features: ['id', 'text'],
    num_rows: 43365
})


In [3]:
import pickle

# Read from file
with open("./predictions/multi_train_val_distilbert.pkl", "rb") as f:
    distilbert_train_val = pickle.load(f)

with open("./predictions/multi_train_val_mdberta.pkl", "rb") as f:
    mdberta_train_val = pickle.load(f)

with open("./predictions/multi_train_val_roberta.pkl", "rb") as f:
    roberta_train_val = pickle.load(f)

with open("./predictions/multi_train_test_distilbert.pkl", "rb") as f:
    distilbert_train_test = pickle.load(f)

with open("./predictions/multi_train_test_mdberta.pkl", "rb") as f:
    mdberta_train_test = pickle.load(f)

with open("./predictions/multi_train_test_roberta.pkl", "rb") as f:
    roberta_train_test = pickle.load(f)

with open("./predictions/multi_test_distilbert.pkl", "rb") as f:
    distilbert_test = pickle.load(f)

with open("./predictions/multi_test_mdberta.pkl", "rb") as f:
    mdberta_test = pickle.load(f)

with open("./predictions/multi_test_roberta.pkl", "rb") as f:
    roberta_test = pickle.load(f)


len(distilbert_train_val), len(mdberta_train_val), len(roberta_train_val), len(distilbert_train_test), len(mdberta_train_test), len(roberta_train_test), len(distilbert_test), len(mdberta_test), len(roberta_test)

(21933, 21933, 21933, 21933, 21933, 21933, 43365, 43365, 43365)

In [4]:
from sklearn.metrics import classification_report, confusion_matrix

def validate_predictions(predictions, dataset):
    # Convert predictions to dictionary for easy lookup
    pred_dict = dict(predictions)

    # Extract ids and labels from dataset
    ids = dataset['id']
    labels = dataset['label']

    # Match predictions with actual labels using ids
    y_true = []
    y_pred = []
    for id, label in zip(ids, labels):
        if id in pred_dict:
            y_true.append(label)
            y_pred.append(1 if pred_dict[id] > 0.5 else 0)  # Assuming binary classification

    # Calculate and print classification report and confusion matrix
    print(classification_report(y_true, y_pred))
    print(confusion_matrix(y_true, y_pred))

# Call the function
validate_predictions(mdberta_train_val, dataset_train["validation"])

              precision    recall  f1-score   support

           0       0.94      0.97      0.95     10151
           1       0.98      0.94      0.96     11782

    accuracy                           0.96     21933
   macro avg       0.96      0.96      0.96     21933
weighted avg       0.96      0.96      0.96     21933

[[ 9871   280]
 [  679 11103]]


In [5]:
import pandas as pd

# Convert each list of predictions to a dictionary
distilbert_dict = dict(distilbert_train_val)
mdberta_dict = dict(mdberta_train_val)
roberta_dict = dict(roberta_train_val)

# Get all unique ids
ids = set(distilbert_dict.keys()).union(mdberta_dict.keys()).union(roberta_dict.keys())

# Create a list of dictionaries, each containing an id and the corresponding predictions
data = []
for id in ids:
    data.append({
        'id': id,
        'pred1': distilbert_dict.get(id, None),
        'pred2': mdberta_dict.get(id, None),
        'pred3': roberta_dict.get(id, None),
    })

# Convert the list of dictionaries to a DataFrame
df_train_val = pd.DataFrame(data)

# Create a dictionary with id as key and text length as value
text_length_dict = {row['id']: len(row['text']) for row in dataset_train["validation"]}

# Add a new column to the DataFrame
df_train_val['text_length'] = df_train_val['id'].map(text_length_dict)

# Create a dictionary with id as key and label as value
label_dict = {row['id']: row['label'] for row in dataset_train["validation"]}

# Add a new column to the DataFrame
df_train_val['label'] = df_train_val['id'].map(label_dict)

df_train_val

id     pred1     pred2     pred3  text_length  label
0      123352  0.996855  0.270851  0.932175         1532      0
1       80493  0.001264  0.001937  0.001647          364      0
2       40612  0.999230  0.998059  0.993848         2011      1
3       91674  0.997733  0.998617  0.993291          317      1
4       84166  0.004268  0.014442  0.007165          191      0
...       ...       ...       ...       ...          ...    ...
21928  128426  0.998801  0.998257  0.990381         1723      1
21929  143697  0.608006  0.825858  0.957722           92      0
21930  149127  0.002662  0.041136  0.010255         1358      0
21931  126403  0.000753  0.001712  0.001272          948      0
21932   57865  0.999255  0.997392  0.995706          513      1

[21933 rows x 6 columns]

In [6]:
import pandas as pd

# Convert each list of predictions to a dictionary
distilbert_dict = dict(distilbert_train_test)
mdberta_dict = dict(mdberta_train_test)
roberta_dict = dict(roberta_train_test)

# Get all unique ids
ids = set(distilbert_dict.keys()).union(mdberta_dict.keys()).union(roberta_dict.keys())

# Create a list of dictionaries, each containing an id and the corresponding predictions
data = []
for id in ids:
    data.append({
        'id': id,
        'pred1': distilbert_dict.get(id, None),
        'pred2': mdberta_dict.get(id, None),
        'pred3': roberta_dict.get(id, None),
    })

# Convert the list of dictionaries to a DataFrame
df_train_test = pd.DataFrame(data)

# Create a dictionary with id as key and text length as value
text_length_dict = {row['id']: len(row['text']) for row in dataset_train["test"]}

# Add a new column to the DataFrame
df_train_test['text_length'] = df_train_test['id'].map(text_length_dict)

# Create a dictionary with id as key and label as value
label_dict = {row['id']: row['label'] for row in dataset_train["test"]}

# Add a new column to the DataFrame
df_train_test['label'] = df_train_test['id'].map(label_dict)

df_train_test

id     pred1     pred2     pred3  text_length  label
0        1309  0.287159  0.986362  0.080024          644      1
1         576  0.999264  0.998628  0.995262          438      1
2      141116  0.992969  0.997976  0.992553         1830      1
3      114729  0.994742  0.997688  0.963934          462      1
4      102369  0.999231  0.996691  0.994334         1776      1
...       ...       ...       ...       ...          ...    ...
21928   95789  0.882732  0.002129  0.174651         1677      0
21929   61256  0.063240  0.011331  0.182544          114      0
21930   13086  0.999306  0.997935  0.995459         1716      1
21931   49428  0.369138  0.206087  0.782119         1865      0
21932  117733  0.968170  0.827757  0.784803          144      1

[21933 rows x 6 columns]

In [7]:
import pandas as pd

# Convert each list of predictions to a dictionary
distilbert_dict = dict(distilbert_test)
mdberta_dict = dict(mdberta_test)
roberta_dict = dict(roberta_test)

# Get all unique ids
ids = set(distilbert_dict.keys()).union(mdberta_dict.keys()).union(roberta_dict.keys())

# Create a list of dictionaries, each containing an id and the corresponding predictions
data = []
for id in ids:
    data.append({
        'id': id,
        'pred1': distilbert_dict.get(id, None),
        'pred2': mdberta_dict.get(id, None),
        'pred3': roberta_dict.get(id, None),
    })

# Convert the list of dictionaries to a DataFrame
df_test = pd.DataFrame(data)

# Create a dictionary with id as key and text length as value
text_length_dict = {row['id']: len(row['text']) for row in dataset_test}

# Add a new column to the DataFrame
df_test['text_length'] = df_test['id'].map(text_length_dict)

# Create a dictionary with id as key and label as value
#label_dict = {row['id']: row['label'] for row in dataset_test}

# Add a new column to the DataFrame
#df_test['label'] = df_test['id'].map(label_dict)

df_test

id     pred1     pred2     pred3  text_length
0       63026  0.014689  0.021168  0.462200          433
1       86908  0.947516  0.806751  0.392055          114
2      122895  0.998951  0.998676  0.992785         1974
3       40292  0.998144  0.642373  0.967956          235
4      123826  0.985256  0.408285  0.990489          444
...       ...       ...       ...       ...          ...
43360  114911  0.998904  0.996565  0.993320          559
43361  121042  0.999043  0.991882  0.991410          605
43362   24410  0.996205  0.972815  0.992176          827
43363   49417  0.799745  0.564137  0.972664          309
43364   92147  0.831145  0.070360  0.990255          433

[43365 rows x 5 columns]

In [24]:
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from torch import nn
from sklearn.metrics import accuracy_score
import torch
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LogisticRegression


class TransformerEnsemble:
    def __init__(self, num_models, ensemble_model=LogisticRegression(max_iter=10000), df_train=None, df_test=None):
        self.num_models = num_models
        self.df_train = df_train
        self.df_test = df_test
        self.ensemble_model = ensemble_model
        self.scaler = StandardScaler()

    def train(self):
        
        
        #df_train, df_test = train_test_split(self.df_train, test_size=0.3, random_state=42)

        print("Predictions shape:", self.df_train.shape)

        X_train = self.df_train.drop(columns=['id', 'label'])
        y_train = self.df_train['label']

        #X_train = self.scaler.fit_transform(X_train)

        #X_test = df_test.drop(columns=['id', 'label'])
        #y_test = df_test['label']

        self.ensemble_model.fit(X_train, y_train)

        #X_test = self.scaler.transform(X_test)

        #y_pred = self.ensemble_model.predict(X_test)

        #print(classification_report(y_test, y_pred))

    def train_grid_search(self):
        # Define the parameter grid
        param_grid = {
            'class_weight': [{0: 100, 1: 1}, {0: 50, 1: 1}, {0: 50, 1: 1}],
            'C': [0.001, 0.01, 0.1, 1, 10, 100, 1000],  # Wider range of regularization parameters
            'solver': ['newton-cg', 'lbfgs', 'liblinear'],  # More solver options
            'penalty': ['l2', 'none'],  # Include no penalty option for solvers that support it
            'tol': [1e-4, 1e-3, 1e-2]  # Different tolerance values for convergence
        }

        # Initialize a Logistic Regression model
        logreg = LogisticRegression(max_iter=10000)

        # Initialize a GridSearchCV object
        grid_search = GridSearchCV(logreg, param_grid, cv=5, scoring='f1_macro')

        # Split the DataFrame into features and target
        X = self.df_train.drop(columns=['id', 'label'])
        y = self.df_train['label']

        # Perform the grid search
        grid_search.fit(X, y)

        # Print the best parameters and the best score
        print("Best parameters:", grid_search.best_params_)
        print("Best score:", grid_search.best_score_)

        # Train the ensemble model using the best parameters
        self.ensemble_model = LogisticRegression(C=grid_search.best_params_['C'], class_weight=grid_search.best_params_['class_weight'])
        self.ensemble_model.fit(X, y)


    def validate(self):
        X_test = self.df_test.drop(columns=['id', 'label'])
        y_test = self.df_test['label']

        #X_test = self.scaler.transform(X_test)

        y_pred = self.ensemble_model.predict(X_test)

        print(classification_report(y_test, y_pred))

    def predict_df(self):

        df_predictions = self.df_test.copy()

        # Get the features from df_test
        X_test = df_predictions

        # Get the predicted labels
        y_pred = self.ensemble_model.predict(X_test.drop(columns=['id']))

        # Get the predicted probabilities
        y_pred_prob = self.ensemble_model.predict_proba(X_test.drop(columns=['id']))

        # Add the predicted labels and probabilities to df_test
        df_predictions['predicted_label'] = y_pred
        df_predictions['predicted_prob'] = y_pred_prob[:, 1]

        return df_predictions

    def predict(self):
        X_test = self.df_test

        y_pred = self.ensemble_model.predict(X_test.drop(columns=['id']))

        # Create a DataFrame with the predictions
        df_pred = pd.DataFrame({
            'id': X_test['id'],
            'label': y_pred
        })

        # Replace the numeric labels with string labels
        df_pred['label'] = df_pred['label'].replace({0 : "human", 1 : "generated"})

        # Convert the DataFrame to a list of dictionaries
        predictions = df_pred.to_dict('records')

        # Print the predictions
        #for prediction in predictions:
        #    print(prediction)

        return predictions



In [9]:
# Read from file

te = TransformerEnsemble(num_models=3, df_train=df_train_val, df_test=df_train_test)

In [10]:
te.train()
te.validate()

Predictions shape: (21933, 6)
              precision    recall  f1-score   support

           0       0.96      0.96      0.96     10145
           1       0.97      0.96      0.97     11788

    accuracy                           0.96     21933
   macro avg       0.96      0.96      0.96     21933
weighted avg       0.96      0.96      0.96     21933



In [11]:
te.train_grid_search()

c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\model_selection\_validation.py:547: FitFailedWarning: 
945 fits failed out of a total of 1890.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
945 fits failed with the following error:
Traceback (most recent call last):
  File "c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 895, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\base.py", line 1467, in wrapper
    estimator._validate_params()
  File "c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\base.py", line 666, in _validate_params
    validate_parameter_constraints(
  File "c:\Users\jorge\miniconda3\Lib\site-

Best parameters: {'C': 1, 'class_weight': {0: 30, 1: 1}, 'penalty': 'l2', 'solver': 'newton-cg', 'tol': 0.001}
Best score: 0.936561577225096


In [12]:
te.validate()

              precision    recall  f1-score   support

           0       0.89      0.99      0.94     10145
           1       0.99      0.90      0.94     11788

    accuracy                           0.94     21933
   macro avg       0.94      0.94      0.94     21933
weighted avg       0.95      0.94      0.94     21933



In [25]:
df_train_def = pd.concat([df_train_val, df_train_test], ignore_index=True)

te = TransformerEnsemble(num_models=3, df_train=df_train_def.drop(columns=['text_length']), df_test=df_test.drop(columns=['text_length']))

In [26]:
te.train()

Predictions shape: (43866, 5)


In [27]:
te.train_grid_search()

Best parameters: {'C': 10, 'class_weight': {0: 50, 1: 1}, 'penalty': 'l2', 'solver': 'liblinear', 'tol': 0.01}
Best score: 0.9290270552063176


c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\model_selection\_validation.py:547: FitFailedWarning: 
945 fits failed out of a total of 1890.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
945 fits failed with the following error:
Traceback (most recent call last):
  File "c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 895, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\base.py", line 1467, in wrapper
    estimator._validate_params()
  File "c:\Users\jorge\miniconda3\Lib\site-packages\sklearn\base.py", line 666, in _validate_params
    validate_parameter_constraints(
  File "c:\Users\jorge\miniconda3\Lib\site-

In [28]:
df_preds = te.predict_df()

In [29]:
proportions = df_preds['predicted_label'].value_counts(normalize=True)
print(proportions)

predicted_label
1    0.502341
0    0.497659
Name: proportion, dtype: float64


In [30]:
df_preds

id     pred1     pred2     pred3  predicted_label  predicted_prob
0       63026  0.014689  0.021168  0.462200                0        0.000061
1       86908  0.947516  0.806751  0.392055                0        0.205438
2      122895  0.998951  0.998676  0.992785                1        0.799785
3       40292  0.998144  0.642373  0.967956                0        0.265713
4      123826  0.985256  0.408285  0.990489                0        0.072104
...       ...       ...       ...       ...              ...             ...
43360  114911  0.998904  0.996565  0.993320                1        0.797709
43361  121042  0.999043  0.991882  0.991410                1        0.792096
43362   24410  0.996205  0.972815  0.992176                1        0.769169
43363   49417  0.799745  0.564137  0.972664                0        0.097172
43364   92147  0.831145  0.070360  0.990255                0        0.004824

[43365 rows x 6 columns]

In [31]:
ens_preds = te.predict()
ens_preds = [{"id": int(pred["id"]), "label": pred["label"]} for pred in ens_preds]

print(ens_preds)

[{'id': 63026, 'label': 'human'}, {'id': 86908, 'label': 'human'}, {'id': 122895, 'label': 'generated'}, {'id': 40292, 'label': 'human'}, {'id': 123826, 'label': 'human'}, {'id': 67508, 'label': 'generated'}, {'id': 72596, 'label': 'human'}, {'id': 45451, 'label': 'generated'}, {'id': 71238, 'label': 'generated'}, {'id': 126090, 'label': 'human'}, {'id': 37033, 'label': 'human'}, {'id': 45048, 'label': 'human'}, {'id': 101849, 'label': 'generated'}, {'id': 11852, 'label': 'generated'}, {'id': 119806, 'label': 'generated'}, {'id': 151302, 'label': 'human'}, {'id': 149690, 'label': 'generated'}, {'id': 1175, 'label': 'generated'}, {'id': 10643, 'label': 'generated'}, {'id': 87934, 'label': 'human'}, {'id': 97741, 'label': 'human'}, {'id': 13329, 'label': 'human'}, {'id': 49519, 'label': 'human'}, {'id': 66098, 'label': 'human'}, {'id': 59576, 'label': 'human'}, {'id': 71615, 'label': 'human'}, {'id': 139842, 'label': 'human'}, {'id': 103138, 'label': 'human'}, {'id': 135988, 'label': 'hu

In [33]:
import json

# Open the file in write mode
with open('jor_isa_ens_multi.jsonl', 'w') as f:
    for entry in ens_preds:
        # Write each dictionary as a separate line in the file
        f.write(json.dumps(entry) + '\n')

In [22]:
max_prob_row = df_preds.loc[df_preds['predicted_prob'].idxmax()]
print(max_prob_row)

id                    19585
pred1              0.999342
pred2               0.99848
pred3              0.998826
predicted_label           1
predicted_prob     0.801384
Name: 27191, dtype: object


In [23]:
row = dataset_test.filter(lambda example: example['id'] == "10267")
text = row['text']
print(text)

['Building your reputation as a mediator takes time and effort. it requires a thorough understanding of the mediation process, a diverse skill set, and an ongoing commitment to professional development. here are some strategies to help you establish a strong reputation as a mediator: gain a solid foundation: start by obtaining comprehensive training in conflict resolution and mediation. this will provide you with a strong understanding of the process, the various approaches to mediation, and the skills needed to effectively facilitate negotiations. consider pursuing additional education and training to enhance your knowledge and skills, such as specialized courses, workshops, or certifications. foster a deep understanding of conflict dynamics: develop a thorough understanding of the psychological and emotional aspects of conflict. this includes recognizing the various stages of conflict, understanding the motivations and behaviors of parties in conflict, and identifying potential barri

In [24]:
df_preds.head(40)

id     pred1     pred2     pred3  predicted_label  predicted_prob
0   109309  0.051318  0.991169  0.987633                0        0.113627
1    20360  0.998427  0.998584  0.992729                1        0.798877
2    65805  0.999027  0.997469  0.992132                1        0.797835
3    70952  0.997240  0.995067  0.987898                1        0.792750
4    25029  0.999067  0.998620  0.994138                1        0.799765
5    18068  0.034504  0.011059  0.958011                0        0.000181
6    11464  0.998485  0.996388  0.989955                1        0.795614
7   104724  0.889958  0.187113  0.989865                0        0.012835
8    97677  0.331783  0.005540  0.127176                0        0.000085
9    27118  0.651128  0.985137  0.987515                1        0.510647
10  152036  0.002673  0.018147  0.493344                0        0.000063
11  105778  0.996635  0.998399  0.986050                1        0.795326
12   85271  0.006751  0.010875  0.578510                0        0.000073
13   11458  0.633028  0.144138  0.985696                0        0.003876
14   95511  0.998790  0.996975  0.994094                1        0.797855
15    5422  0.996579  0.997007  0.991478                1        0.795704
16  106770  0.242730  0.991458  0.978741                0        0.199476
17   43182  0.416783  0.010964  0.236984                0        0.000150
18  113756  0.258029  0.996946  0.988239                0        0.217786
19   62506  0.987181  0.997893  0.991829                1        0.791295
20   38438  0.006010  0.015080  0.807171                0        0.000122
21   90015  0.182426  0.005003  0.462826                0        0.000102
22  108272  0.992320  0.784757  0.990616                0        0.487166
23   29768  0.010037  0.045263  0.718800                0        0.000124
24   18777  0.993495  0.906381  0.988323                1        0.678458
25   28315  0.863092  0.603106  0.939907                0        0.140193
26   11680  0.862358  0.865931  0.985560                1        0.501988
27   62857  0.991175  0.997241  0.989673                1        0.792171
28  125370  0.018328  0.064405  0.980309                0        0.000255
29   15065  0.996281  0.997711  0.990582                1        0.795970
30   44579  0.794304  0.984816  0.990341                1        0.635662
31  139497  0.997535  0.991737  0.992493                1        0.790946
32   25694  0.998304  0.997939  0.992447                1        0.798026
33   19136  0.896173  0.990321  0.982331                1        0.718779
34   71615  0.334445  0.044462  0.960459                0        0.000661
35   79024  0.047045  0.915081  0.988582                0        0.071285
36   11560  0.785822  0.563755  0.939340                0        0.087177
37  141143  0.997508  0.987378  0.991769                1        0.785894
38   85389  0.797497  0.776405  0.905586                0        0.272307
39   75252  0.979023  0.991041  0.992263                1        0.778962

In [25]:
row = dataset_test.filter(lambda example: example['id'] == "72799")
text = row['text']
print(text)

['Familiarize-se com os diferentes tipos de risco. a maioria dos riscos financeiros pode ser categorizada como sistemáticos ou não sistemáticos. o risco sistemático afeta toda a economia e todas as empresas dentro dela; um exemplo de risco sistemático seria perdas devido a uma recessão. os riscos não sistemáticos são aqueles que variam entre empresas ou setores. esses riscos podem ser minimizados através de um planejamento']


# SVM preds

In [34]:
import pickle

# Read from file
with open("./predictions/svm_test_ca.pkl", "rb") as f:
    svm_preds_ca = pickle.load(f)

with open("./predictions/svm_test_en.pkl", "rb") as f:
    svm_preds_en = pickle.load(f)

with open("./predictions/svm_test_es.pkl", "rb") as f:
    svm_preds_es = pickle.load(f)

with open("./predictions/svm_test_eu.pkl", "rb") as f:
    svm_preds_eu = pickle.load(f)

with open("./predictions/svm_test_gl.pkl", "rb") as f:
    svm_preds_gl = pickle.load(f)

with open("./predictions/svm_test_pt.pkl", "rb") as f:
    svm_preds_pt = pickle.load(f)

len(svm_preds_ca), len(svm_preds_en), len(svm_preds_es), len(svm_preds_eu), len(svm_preds_gl), len(svm_preds_pt)    

(8013, 10324, 9116, 5518, 1391, 9003)

In [35]:
# Concatenate all prediction lists
svm_preds = svm_preds_ca + svm_preds_en + svm_preds_es + svm_preds_eu + svm_preds_gl + svm_preds_pt

# Convert each prediction into a dictionary with the format {"id": 13, "label": "generated"}
svm_preds = [{"id": int(id), "label": "human" if label == 0 else "generated"} for id, label in svm_preds]

print(svm_preds)

[{'id': 146484, 'label': 'generated'}, {'id': 35684, 'label': 'generated'}, {'id': 97370, 'label': 'generated'}, {'id': 33527, 'label': 'generated'}, {'id': 1536, 'label': 'generated'}, {'id': 2218, 'label': 'human'}, {'id': 90386, 'label': 'generated'}, {'id': 99221, 'label': 'generated'}, {'id': 48115, 'label': 'human'}, {'id': 22444, 'label': 'generated'}, {'id': 89771, 'label': 'generated'}, {'id': 138112, 'label': 'generated'}, {'id': 20447, 'label': 'generated'}, {'id': 82743, 'label': 'generated'}, {'id': 146053, 'label': 'generated'}, {'id': 60634, 'label': 'generated'}, {'id': 80863, 'label': 'human'}, {'id': 109338, 'label': 'human'}, {'id': 45008, 'label': 'generated'}, {'id': 14579, 'label': 'generated'}, {'id': 132908, 'label': 'generated'}, {'id': 44730, 'label': 'human'}, {'id': 104505, 'label': 'human'}, {'id': 134934, 'label': 'generated'}, {'id': 78331, 'label': 'generated'}, {'id': 106420, 'label': 'generated'}, {'id': 79648, 'label': 'generated'}, {'id': 12691, 'lab

In [36]:
import json

# Open the file in write mode
with open('jor_isa_ld_svm.jsonl', 'w') as f:
    for entry in svm_preds:
        # Write each dictionary as a separate line in the file
        f.write(json.dumps(entry) + '\n')

In [23]:
# Get the prediction with id 146484
prediction = next((pred for pred in svm_preds if pred['id'] == 72799), None)

print(prediction)

{'id': 72799, 'label': 'human'}


In [37]:
# Count the occurrences of each label
counts = {"human": 0, "generated": 0}
for pred in svm_preds:
    counts[pred["label"]] += 1

# Calculate the proportions
total = len(svm_preds)
proportions = {label: count / total for label, count in counts.items()}

print(proportions)

{'human': 0.2965986394557823, 'generated': 0.7034013605442176}


In [26]:
# Make sure both lists are sorted by id
svm_preds.sort(key=lambda x: x['id'])
ens_preds.sort(key=lambda x: int(x['id']))

# Get the indices where the predictions agree
agreement_indices = [i for i, (svm_pred, ens_pred) in enumerate(zip(svm_preds, ens_preds)) if svm_pred['label'] == ens_pred['label']]

print(agreement_indices)

[0, 2, 3, 5, 7, 9, 10, 13, 14, 16, 17, 18, 19, 20, 21, 23, 25, 27, 28, 29, 30, 31, 32, 33, 34, 36, 38, 39, 40, 42, 43, 44, 45, 46, 47, 48, 50, 51, 52, 54, 56, 58, 59, 61, 62, 63, 64, 65, 66, 68, 69, 70, 71, 72, 74, 75, 76, 77, 78, 79, 80, 81, 83, 84, 86, 87, 89, 90, 91, 92, 94, 95, 96, 98, 100, 101, 103, 104, 105, 106, 107, 110, 111, 112, 114, 115, 118, 121, 125, 126, 127, 128, 129, 131, 133, 135, 136, 137, 141, 144, 145, 146, 148, 149, 150, 155, 156, 160, 161, 162, 163, 165, 166, 167, 168, 170, 171, 172, 173, 174, 176, 177, 179, 180, 183, 184, 187, 189, 192, 193, 194, 195, 196, 198, 201, 203, 204, 205, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 219, 221, 222, 223, 225, 226, 227, 228, 229, 230, 232, 233, 236, 237, 239, 240, 241, 244, 247, 248, 249, 250, 251, 252, 253, 254, 255, 256, 258, 264, 266, 267, 268, 270, 271, 272, 275, 276, 278, 279, 282, 283, 285, 288, 289, 291, 292, 293, 295, 296, 298, 299, 300, 301, 303, 304, 305, 306, 308, 309, 310, 311, 312, 314, 315, 317, 318,

In [27]:
# Calculate the proportion of agreement
agreement_proportion = len(agreement_indices) / len(svm_preds)

print(agreement_proportion)

0.6583189207886544


In [28]:
# Initialize the counts
svm_preds.sort(key=lambda x: x['id'])
ens_preds.sort(key=lambda x: int(x['id']))

counts = {"human": 0, "generated": 0}
total_counts = {"human": 0, "generated": 0}

# Count the agreements and total predictions for each class
for svm_pred, ens_pred in zip(svm_preds, ens_preds):
    if svm_pred['label'] == ens_pred['label']:
        counts[svm_pred['label']] += 1
    total_counts[svm_pred['label']] += 1

# Calculate the proportions
proportions = {label: counts[label] / total_counts[label] for label in counts}

print(proportions)

{'human': 0.7629451096252526, 'generated': 0.6142018817821198}


# TRANSFORMERS POR LENGUAJE

In [38]:
import pickle

# Read from file
with open("./predictions/tr_test_ca.pkl", "rb") as f:
    tr_preds_ca = pickle.load(f)

with open("./predictions/tr_test_en.pkl", "rb") as f:
    tr_preds_en = pickle.load(f)

with open("./predictions/tr_test_es.pkl", "rb") as f:
    tr_preds_es = pickle.load(f)

with open("./predictions/tr_test_eu.pkl", "rb") as f:
    tr_preds_eu = pickle.load(f)

with open("./predictions/tr_test_gl.pkl", "rb") as f:
    tr_preds_gl = pickle.load(f)

with open("./predictions/tr_test_pt.pkl", "rb") as f:
    tr_preds_pt = pickle.load(f)


len(tr_preds_ca), len(tr_preds_en), len(tr_preds_es), len(tr_preds_eu), len(tr_preds_gl), len(tr_preds_pt)

(8013, 10324, 9116, 5518, 1391, 9003)

In [39]:
all_preds = tr_preds_ca + tr_preds_en + tr_preds_es + tr_preds_eu + tr_preds_gl + tr_preds_pt

#all_preds

In [40]:
# Convert each prediction into a dictionary with the format {"id": 13, "label": "generated"}
trans_preds = [{"id": int(id), "label": "human" if prob < 0.999 else "generated"} for id, prob in all_preds]

#print(trans_preds)

In [41]:
# Count the occurrences of each label
counts = {"human": 0, "generated": 0}
for pred in trans_preds:
    counts[pred["label"]] += 1

# Calculate the proportions
total = len(trans_preds)
proportions = {label: count / total for label, count in counts.items()}

print(proportions)

{'human': 0.49844344517468003, 'generated': 0.5015565548253199}


In [42]:
import json

# Open the file in write mode
with open('jor_isa_ld_transf.jsonl', 'w') as f:
    for entry in trans_preds:
        # Write each dictionary as a separate line in the file
        f.write(json.dumps(entry) + '\n')

In [34]:
# Make sure both lists are sorted by id
svm_preds.sort(key=lambda x: x['id'])
ens_preds.sort(key=lambda x: int(x['id']))
trans_preds.sort(key=lambda x: x['id'])

# Get the indices where the predictions agree
agreement_indices_svm_ens = [i for i, (svm_pred, ens_pred) in enumerate(zip(svm_preds, ens_preds)) if svm_pred['label'] == ens_pred['label']]

agreement_indices_svm_trans = [i for i, (svm_pred, trans_preds) in enumerate(zip(svm_preds, trans_preds)) if svm_pred['label'] == trans_preds['label']]

agreement_indices_ens_trans = [i for i, (ens_preds, trans_preds) in enumerate(zip(ens_preds, trans_preds)) if ens_preds['label'] == trans_preds['label']]

In [35]:
# Calculate the proportion of agreement
agreement_proportion_svm_ens = len(agreement_indices_svm_ens) / len(svm_preds)

agreement_proportion_svm_trans = len(agreement_indices_svm_trans) / len(svm_preds)

agreement_proportion_ens_trans = len(agreement_indices_ens_trans) / len(svm_preds)

print(agreement_proportion_svm_ens)
print(agreement_proportion_svm_trans)
print(agreement_proportion_ens_trans)

0.6583189207886544
0.650893577770091
0.7890464660440447


In [43]:

test_ids = set(int(id) for id in dataset_test['id'])

# Assuming ens_preds, trans_preds, and svm_preds are dictionaries with 'id' as keys
ens_ids = set(d['id'] for d in ens_preds)
trans_ids = set(d['id'] for d in trans_preds)
svm_ids = set(d['id'] for d in svm_preds)

# Check if all ids in test_ids are in ens_ids, trans_ids, and svm_ids
print("All test ids are in ens_preds:", test_ids.issubset(ens_ids))
print("All test ids are in trans_preds:", test_ids.issubset(trans_ids))
print("All test ids are in svm_preds:", test_ids.issubset(svm_ids))

# Check if the number of samples are the same
print("Number of samples are the same in test and ens_preds:", len(test_ids) == len(ens_ids))
print("Number of samples are the same in test and trans_preds:", len(test_ids) == len(trans_ids))
print("Number of samples are the same in test and svm_preds:", len(test_ids) == len(svm_ids))

All test ids are in ens_preds: True
All test ids are in trans_preds: True
All test ids are in svm_preds: True
Number of samples are the same in test and ens_preds: True
Number of samples are the same in test and trans_preds: True
Number of samples are the same in test and svm_preds: True


In [44]:
# Count the occurrences of each label
counts = {"human": 0, "generated": 0}
for pred in svm_preds:
    counts[pred["label"]] += 1

# Calculate the proportions
total = len(svm_preds)
proportions = {label: count / total for label, count in counts.items()}

print("svm proportions:\n", proportions)

svm proportions:
 {'human': 0.2965986394557823, 'generated': 0.7034013605442176}


In [45]:
# Count the occurrences of each label
counts = {"human": 0, "generated": 0}
for pred in ens_preds:
    counts[pred["label"]] += 1

# Calculate the proportions
total = len(ens_preds)
proportions = {label: count / total for label, count in counts.items()}

print("ens proportions:\n", proportions)

ens proportions:
 {'human': 0.4976594027441485, 'generated': 0.5023405972558515}


In [46]:
# Count the occurrences of each label
counts = {"human": 0, "generated": 0}
for pred in trans_preds:
    counts[pred["label"]] += 1

# Calculate the proportions
total = len(trans_preds)
proportions = {label: count / total for label, count in counts.items()}

print("ens proportions:\n", proportions)

ens proportions:
 {'human': 0.49844344517468003, 'generated': 0.5015565548253199}


In [1]:
svm_preds

NameError: name 'svm_preds' is not defined